In [2]:
import requests
from bs4 import BeautifulSoup
import numpy as np
import pandas as pd
import json
import time
import re
import os
import konlpy.tag
from ckonlpy.tag import Twitter as cTwitter
import wordcloud
import matplotlib.pyplot as plt
%matplotlib inline
import codecs
from gensim.models import word2vec
from collections import Counter

---
## [이용 가이드]

#### 첫번째 셀 : 기본설정 및 크롤링
- 사용자 설정 있음

> `start_page` : 크롤링할 시작 페이지  
> `resresh_unit` : 새로고침 단위 (320 페이지 이상 이동시 크롬 out of memory 발생  
> `stop_page` : 크롤링할 마지막 페이지  
> `file_name` : 저장할 파일명  
- .기호 개당 1초를 의미 <- 사용자 정의 함수 delay(str, int)

#### 두번째 셀 : 데이터 저장

#### 세번째 셀 : 저장된 데이터 확인
- 윈도우에서 인코딩 형식 디스매칭으로 글자 깨질 때 사용하기에 유용
- 인덱스 번호와 게시물 번호 매칭하여 데이터 누락/중복 확인 가능

---

In [155]:
# 첫번째 셀 : 기본설정
# 크롤링을 위해 사용자가 입력해야 되는 값
start_page = 1    # 크롤링할 시작 페이지
refresh_unit = 200   # 크롤링 후 새로고침할 단위
stop_page = 1111   # 크롤링할 마지막 페이지
file_name = 'patent_{date}_{first_page}_{last_page}.csv'  # 저장할 파일명

# 메인
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.keys import Keys
from IPython.display import Image
from bs4 import BeautifulSoup
import pandas as pd
from datetime import datetime
import time
import os
import math

# 함수 : 딜레이
def delay(text, sec):
    print(text, end="")
    for i in range(sec): print('.', end=""); time.sleep(1)

# 함수 : 사이트에서 제목/내용 크롤링
current_page_css_selector = 'span.board_pager03 strong'
def contentCrawling(current_page_css_selector = current_page_css_selector):
    dom = BeautifulSoup(driver.page_source, 'html.parser')
    patent_list = dom.select('.search_section article')
    
    current_page = driver.find_element_by_css_selector(current_page_css_selector).text

    result = [
            {
                '제목': patent.select_one('.search_section_title h1 > a:nth-of-type(2)').text.strip(),
                '내용': patent.select_one('.search_txt').text.strip()
            }
            for patent in patent_list
    ]

    return int(current_page), result   # (크롤링한 페이지, 크롤링 결과) 반환

# 함수 : 저장할 파일 경로 찾기
def findPath(file_name):
    file_path = r'D:\DevRoot\StockHelper\dataset'
    file_name = file_name
    try: 
        path = os.path.join(file_path, file_name)
    except(Exception):
        file_path = 'C:\DeepLearning_Project\StockHelper\StockHelper\dataset'
        path = os.path.join(file_path, file_name)
        
    return path

print('프로그램 시작')
start = time.time()  # 시작 시간 저장
result = []

# 1. webdriver를 이용해 kipris 접속
driver_path = r'D:\DevRoot\download\chromedriver.exe'
try: 
    driver = webdriver.Chrome(driver_path)
except(Exception):
    driver_path = r'C:\DevRoot\download\chromedriver.exe'
    driver = webdriver.Chrome(driver_path)

for refreshed_num in range(1, math.ceil(stop_page / refresh_unit) + 1):
    driver.get("http://kpat.kipris.or.kr/kpat/searchLogina.do?next=MainSearch")
    
    # 크롤링 시작페이지 재설정
    if refreshed_num != 1: start_page = refresh_unit * (refreshed_num - 1) + 1
    
    # 2. 검색 옵션 설정
    delay('검색 옵션 설정', 4)

    # 2.1. 행정상태 변경
    # defalut 해제 <- '전체' 클릭
    driver.find_element_by_css_selector('form#leftside .release_list > span:nth-of-type(1) > input').click()
    # 원하는 checkbox만 선택 <- '등록' 클릭
    driver.find_element_by_css_selector('form#leftside .release_list > span:nth-last-of-type(1) > input').click()

    # 2.2. 기간을 검색어로 입력
    today = datetime.today().strftime("%Y%m%d")
    decade = str(int(today) - int('00001000'))
    driver.find_element_by_css_selector('.keyword').send_keys(f'GD=[{decade}~{today}]')
    driver.find_element_by_css_selector('.input_btn img').click()

    # 2.3. 90개씩 보기 선택
    pageSel = 90   # 페이지당 게시물 개수 (30, 60, 90 중 택1)
    select = Select(driver.find_element_by_id('opt28'))
    select.select_by_value(str(pageSel))
    driver.find_element_by_css_selector('#pageSel img').click()

    print('검색 완료')

    # 3. 데이터 추출
    delay('데이터 추출 준비중', 3)
    print('완료')

    page_num = 'span.board_pager03 a:nth-last-of-type({0})'   # target_page 구할 때 이용

    # 3.1. 첫 페이지 크롤링
    current_page, data = contentCrawling()
    if current_page == stop_page: break   # 실행종료
    if current_page != start_page:   # 첫 페이지 찾기
        delay('시작 페이지로 이동', 0)
        while current_page < start_page:
            if current_page // 10 < start_page // 10:
                driver.find_element_by_css_selector(page_num.format(1)).click()
                delay('', 2)
                current_page = int(driver.find_element_by_css_selector(current_page_css_selector).text)
                continue
            for i in range(10, 0, -1):
                driver.find_element_by_css_selector(page_num.format(i)).click()
                delay('', 2)
                current_page = int(driver.find_element_by_css_selector(current_page_css_selector).text)
                if current_page == start_page: print('완료'); break
    current_page, data = contentCrawling()
    result.extend(data)
    print(f'{current_page} 위치 -> {current_page} 페이지 크롤링 완료')

    # 3.2. 페이지 이동하며 크롤링
    while True:
        # 실행 종료
        if current_page >= stop_page: break
        if current_page == refresh_unit * refreshed_num: break

        for i in range(10, 0, -1):
            if current_page >= stop_page: break
            if current_page == refresh_unit * refreshed_num: break

            # 3.2.1. 크롤링할 페이지가 현재 페이지의 다음 페이지인 지 확인
            target_page = driver.find_element_by_css_selector(page_num.format(i))
            if i != 1 and int(target_page.text) <= current_page: delay('', 1); continue 

            print(f'현재 {current_page}', end=" -> ")
            time.sleep(1)
            # 3.2.2. 크롤링할 페이지(target_page)인 다음 페이지로 이동
            print(f'{target_page.text} click', end=" -> ")
            target_page.click()  # 크롤링할 페이지로 이동
            delay('', 2)        
            while True:
                click_page = driver.find_element_by_css_selector(current_page_css_selector).text
    #             try: # (클릭해서 이동한) 현재 페이지(click_page)는 target_page
    #                 click_page = driver.find_element_by_css_selector(current_page_css_selector).text
    #             except KeyboardInterrupt or WebDriverException:
    #                 print('Interrupted')
    #                 try: sys.exit(0)
    #                 except SystemExit: os._exit(0)
    #                 finally:
    #                     print('긁어온 데이터개수 :', len(result))
    #                     print('소요시간 :', int(time.time() - start) / 60, '분')  # 현재시각 - 시작시간 = 실행 시간
    #                     print('프로그램 종료')
    #             except Exception:
    #                 driver.refresh()   # 새로고침
    #                 dealy('', 4)
    #                 dom = BeautifulSoup(driver.page_source, 'html.parser')
    #                 patent_list = dom.select('.search_section article')
    #                 click_page = int(driver.find_element_by_css_selector(current_page_css_selector).text)

                if current_page != click_page: break  # 페이지 이동 시 loop 탈출
                delay("", 2)  # 페이지 이동 안 하면 seelp()
            # 3.2.3. 크롤링
            current_page, data = contentCrawling()
            result.extend(data)
            # 3.2.4. 중간결과 반환
            print(f'{current_page} 페이지 크롤링 완료')

print('=' * 60)
print('긁어온 데이터개수 :', len(result))
print('소요시간 :', int(time.time() - start) / 60, '분')  # 현재시각 - 시작시간 = 실행 시간
print('프로그램 종료')

프로그램 시작
검색 옵션 설정....검색 완료
데이터 추출 준비중...완료
1 위치 -> 1 페이지 크롤링 완료
현재 1 -> 2 click -> ..2 페이지 크롤링 완료
현재 2 -> 3 click -> ..3 페이지 크롤링 완료
현재 3 -> 4 click -> ..4 페이지 크롤링 완료
현재 4 -> 5 click -> ..5 페이지 크롤링 완료
현재 5 -> 6 click -> ..6 페이지 크롤링 완료
현재 6 -> 7 click -> ..7 페이지 크롤링 완료
현재 7 -> 8 click -> ..8 페이지 크롤링 완료
현재 8 -> 9 click -> ..9 페이지 크롤링 완료
현재 9 -> 10 click -> ..10 페이지 크롤링 완료
현재 10 -> 다음 click -> ..11 페이지 크롤링 완료
현재 11 -> 12 click -> ..12 페이지 크롤링 완료
현재 12 -> 13 click -> ..13 페이지 크롤링 완료
현재 13 -> 14 click -> ..14 페이지 크롤링 완료
현재 14 -> 15 click -> ..15 페이지 크롤링 완료
현재 15 -> 16 click -> ..16 페이지 크롤링 완료
현재 16 -> 17 click -> ..17 페이지 크롤링 완료
현재 17 -> 18 click -> ..18 페이지 크롤링 완료
현재 18 -> 19 click -> ..19 페이지 크롤링 완료
현재 19 -> 20 click -> ..20 페이지 크롤링 완료
현재 20 -> 다음 click -> ..21 페이지 크롤링 완료
현재 21 -> 22 click -> ..22 페이지 크롤링 완료
현재 22 -> 23 click -> ..23 페이지 크롤링 완료
현재 23 -> 24 click -> ..24 페이지 크롤링 완료
현재 24 -> 25 click -> ..25 페이지 크롤링 완료
현재 25 -> 26 click -> ..26 페이지 크롤링 완료
현재 26 -> 27 click -> ..27 페이지 크롤링 완료


현재 211 -> 212 click -> ..212 페이지 크롤링 완료
현재 212 -> 213 click -> ..213 페이지 크롤링 완료
현재 213 -> 214 click -> ..214 페이지 크롤링 완료
현재 214 -> 215 click -> ..215 페이지 크롤링 완료
현재 215 -> 216 click -> ..216 페이지 크롤링 완료
현재 216 -> 217 click -> ..217 페이지 크롤링 완료
현재 217 -> 218 click -> ..218 페이지 크롤링 완료
현재 218 -> 219 click -> ..219 페이지 크롤링 완료
현재 219 -> 220 click -> ..220 페이지 크롤링 완료
현재 220 -> 다음 click -> ..221 페이지 크롤링 완료
현재 221 -> 222 click -> ..222 페이지 크롤링 완료
현재 222 -> 223 click -> ..223 페이지 크롤링 완료
현재 223 -> 224 click -> ..224 페이지 크롤링 완료
현재 224 -> 225 click -> ..225 페이지 크롤링 완료
현재 225 -> 226 click -> ..226 페이지 크롤링 완료
현재 226 -> 227 click -> ..227 페이지 크롤링 완료
현재 227 -> 228 click -> ..228 페이지 크롤링 완료
현재 228 -> 229 click -> ..229 페이지 크롤링 완료
현재 229 -> 230 click -> ..230 페이지 크롤링 완료
현재 230 -> 다음 click -> ..231 페이지 크롤링 완료
현재 231 -> 232 click -> ..232 페이지 크롤링 완료
현재 232 -> 233 click -> ..233 페이지 크롤링 완료
현재 233 -> 234 click -> ..234 페이지 크롤링 완료
현재 234 -> 235 click -> ..235 페이지 크롤링 완료
현재 235 -> 236 click -> ..236 페이지 크롤링 완료
현재

현재 614 -> 615 click -> ..615 페이지 크롤링 완료
현재 615 -> 616 click -> ..616 페이지 크롤링 완료
현재 616 -> 617 click -> ..617 페이지 크롤링 완료
현재 617 -> 618 click -> ..618 페이지 크롤링 완료
현재 618 -> 619 click -> ..619 페이지 크롤링 완료
현재 619 -> 620 click -> ..620 페이지 크롤링 완료
현재 620 -> 다음 click -> ..621 페이지 크롤링 완료
현재 621 -> 622 click -> ..622 페이지 크롤링 완료
현재 622 -> 623 click -> ..623 페이지 크롤링 완료
현재 623 -> 624 click -> ..624 페이지 크롤링 완료
현재 624 -> 625 click -> ..625 페이지 크롤링 완료
현재 625 -> 626 click -> ..626 페이지 크롤링 완료
현재 626 -> 627 click -> ..627 페이지 크롤링 완료
현재 627 -> 628 click -> ..628 페이지 크롤링 완료
현재 628 -> 629 click -> ..629 페이지 크롤링 완료
현재 629 -> 630 click -> ..630 페이지 크롤링 완료
현재 630 -> 다음 click -> ..631 페이지 크롤링 완료
현재 631 -> 632 click -> ..632 페이지 크롤링 완료
현재 632 -> 633 click -> ..633 페이지 크롤링 완료
현재 633 -> 634 click -> ..634 페이지 크롤링 완료
현재 634 -> 635 click -> ..635 페이지 크롤링 완료
현재 635 -> 636 click -> ..636 페이지 크롤링 완료
현재 636 -> 637 click -> ..637 페이지 크롤링 완료
현재 637 -> 638 click -> ..638 페이지 크롤링 완료
현재 638 -> 639 click -> ..639 페이지 크롤링 완료
현재

현재 1012 -> 1013 click -> ..1013 페이지 크롤링 완료
현재 1013 -> 1014 click -> ..1014 페이지 크롤링 완료
현재 1014 -> 1015 click -> ..1015 페이지 크롤링 완료
현재 1015 -> 1016 click -> ..1016 페이지 크롤링 완료
현재 1016 -> 1017 click -> ..1017 페이지 크롤링 완료
현재 1017 -> 1018 click -> ..1018 페이지 크롤링 완료
현재 1018 -> 1019 click -> ..1019 페이지 크롤링 완료
현재 1019 -> 1020 click -> ..1020 페이지 크롤링 완료
현재 1020 -> 다음 click -> ..1021 페이지 크롤링 완료
현재 1021 -> 1022 click -> ..1022 페이지 크롤링 완료
현재 1022 -> 1023 click -> ..1023 페이지 크롤링 완료
현재 1023 -> 1024 click -> ..1024 페이지 크롤링 완료
현재 1024 -> 1025 click -> ..1025 페이지 크롤링 완료
현재 1025 -> 1026 click -> ..1026 페이지 크롤링 완료
현재 1026 -> 1027 click -> ..1027 페이지 크롤링 완료
현재 1027 -> 1028 click -> ..1028 페이지 크롤링 완료
현재 1028 -> 1029 click -> ..1029 페이지 크롤링 완료
현재 1029 -> 1030 click -> ..1030 페이지 크롤링 완료
현재 1030 -> 다음 click -> ..1031 페이지 크롤링 완료
현재 1031 -> 1032 click -> ..1032 페이지 크롤링 완료
현재 1032 -> 1033 click -> ..1033 페이지 크롤링 완료
현재 1033 -> 1034 click -> ..1034 페이지 크롤링 완료
현재 1034 -> 1035 click -> ..1035 페이지 크롤링 완료
현재 1035 -> 1036

In [165]:
# 세번째 셀 : 데이터 저장
# 데이터 저장 : list -> df -> csv 저장
file_name = file_name.format(date=today, first_page=1, last_page=len(result) // 90)
path = findPath(file_name)
pd.DataFrame(result, index=range(1, len(result) + 1)).to_csv(path, encoding='utf-8')

# 저장 결과 반환
if os.path.isfile(path):
    print('>>> 파일변환 완료:', datetime.today().strftime(("%Y-%m-%d %H:%M:%S")))
    print('>>> 저장위치:', path)
else: print('>>> 파일변환 실패')

>>> 파일변환 완료: 2021-12-03 09:12:15
>>> 저장위치: D:\DevRoot\StockHelper\dataset\patent_20211203_1_1111.0.csv


In [ ]:
# 네번째 셀 : 저장된 데이터 확인
file_name = file_name.format(date=today)
path = findPath(file_name)
pd.read_csv(path).style.hide_index()

In [4]:
patent_info = pd.read_csv(r'C:\DeepLearning_Project\StockHelper\StockHelper\dataset\patent_20211203_1_200.csv')
patent_info = patent_info.iloc[:,1:]
patent_info

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\DeepLearning_Project\\StockHelper\\StockHelper\\dataset\\patent_20211203_1_200.csv'

In [6]:
patent_info = pd.read_csv(r'C:\DeepLearning_Project\StockHelper\dataset\patent_20211203_1_200.csv')
patent_info = patent_info.iloc[:,1:]
patent_info

제목  \
0      절취 가능한 환자용 매트리스 커버(Cuttable patient mattress c...   
1                                       스케치북(sketchbook)   
2      물배출구 오염이 방지되는 편향물통뚜껑(Deflection bottle cap to ...   
3      골프 힙턴 트레이닝 장치(TRAINING DEVICE FOR HIP-TURN OF ...   
4      다이아프램 밸브를 포함하는 유압부의 유량 감지장치(Apparatus of sensi...   
...                                                  ...   
17995  전기장 셰이핑 장치 및 전기장을 이용한 타겟 처리 장치(ELECTRIC FIELD ...   
17996  충격 흡수와 롤링 보행을 위한 신발 물품(FOOT WEAR FOR IMPACT AB...   
17997  폴리이미드 바니시 및 그의 제조 방법(POLYIMIDE VARNISH AND MET...   
17998  순환 고듀티비 펄스 방전 다기능성 나노 보호코팅층 제조방법(METHOD FOR PR...   
17999                  스위칭 전원 장치(SWITCHING POWER SUPPLY)   

                                                      내용  
0      본 고안은 부직포층과 방수층으로 이루어지는 복수개의 시트부를 적층하여 절취 가능하도...  
1      스케치북을 개시한다. 본 개시의 일 실시예에 의하면, 복수의 용지가 적층되어 구성되...  
2      본 발명은 물통의 상부에 결합되는 편향물통뚜껑에 관한 것으로서, 물통의 상부에 개폐...  
3      본 고안에 따른 골프 힙턴 트레이닝 장치는 띠 형상으로 타측에 제1고리부재가 결합되...  
4      다이아프램 밸브의 손상 및 유체누설을 사전에 감지하여 제품의 불량을 방지하고 비정상...  
...                                                  ...  
17995  본 실시예에 의한 전기장 셰이핑 장치는 기판과, 기판 상에 위치하는 제1 전극과, ...  
17996  본 발명의 신발 물품은 중앙 힌지부, 중앙 힌지부로부터 전방 하부로 연장된 전방 다...  
17997  본 발명은, 투명성이 높으면서 또한 복수회의 굴곡에 대한 굴곡 내성이 개선된 폴리이...  
17998  본 발명의 순환 고듀티비 펄스 방전 다기능성 나노 보호코팅층 제조방법은 플라즈마 기...  
17999  본 발명은 전원 효율을 향상시킬 수 있는 스위칭 전원 장치를 개시한다. 상기 스위칭...  

[18000 rows x 2 columns]

In [7]:
twitter = konlpy.tag.Twitter()
nlp = twitter   # Customized Konlpy


name_pos = {
    "Noun" : "명사"
}

patent_info_str = ""

for title in patent_info.제목 :
    patent_info_str += title
    
for content in patent_info.내용 :
    patent_info_str += content
    

def sep_pos(article):
    # 기사의 어휘소 분석
    morphs = nlp.pos(article, norm=True, stem=True)
     
    pos_words = []
                     
    for pos in name_pos:  # "Noun", "Verb"  통계검색할 품사들
        
        for mal in morphs:
            # 통계집계할 단어품사만 and 단어길이가 2글자 이상만
            if pos == mal[1]:  
                pos_words.append(mal)  # 단어 추가
           
    return pos_words


C:\ProgramData\Anaconda3\lib\site-packages\konlpy\tag\_okt.py:16: UserWarning: "Twitter" has changed to "Okt" since KoNLPy v0.4.5.
  warn('"Twitter" has changed to "Okt" since KoNLPy v0.4.5.')


In [8]:
patent_info_str

'절취 가능한 환자용 매트리스 커버(Cuttable patient mattress cover)스케치북(sketchbook)물배출구 오염이 방지되는 편향물통뚜껑(Deflection bottle cap to prevent water outlet contamination)골프 힙턴 트레이닝 장치(TRAINING DEVICE FOR HIP-TURN OF GOLF)다이아프램 밸브를 포함하는 유압부의 유량 감지장치(Apparatus of sensing flow rate of fluid pressure part having diaphragm valve)비닐봉투 고정구가 구비된 물품 수거함(Article collection box with plastic bag fixture)오일 회로 및 오일 회로를 구비한 무오일 압축기(OIL CIRCUIT, OIL-FREE COMPRESSOR PROVIDED WITH SUCH OIL CIRCUIT AND A METHOD TO CONTROL LUBRICATION AND/OR COOLING OF SUCH OIL-FREE COMPRESSOR VIA SUCH OIL CIRCUIT)엘리베이터용 로울러 가이드장치(Roller guide device for elevator)장식줄의 길이 조절이 가능한 장신구(ACCESSORY FOR LENGTH ADJUSTABLE OF DECORATIVE STRING)착즙 주스기용 스크류 및 이를 사용하는 착즙 주스기(SCREW FOR JUICING AND JUICER USING THE SAME)회전 이동 가능한 프레임 구조물(Frame structure capable of rotational movement)골프 힙턴 타이밍 연습기(Golf Hip Turn Timing Trainer)구이용 불판(Grill Plate For Roasting)유지 보수성이 향상된 지반굴착용 교반 비트의 바이트 팁(BITE TIP OF AGITATING BIT FOR GROUND EXCAVATION WITH IMPROVED MAINTA

In [9]:
sep_pos(patent_info_str)

[('절취', 'Noun'),
 ('환자', 'Noun'),
 ('용', 'Noun'),
 ('매트리스', 'Noun'),
 ('커버', 'Noun'),
 ('스케치북', 'Noun'),
 ('물배', 'Noun'),
 ('출구', 'Noun'),
 ('오염', 'Noun'),
 ('방지', 'Noun'),
 ('편향', 'Noun'),
 ('물통', 'Noun'),
 ('뚜껑', 'Noun'),
 ('골프', 'Noun'),
 ('힙턴', 'Noun'),
 ('트레이닝', 'Noun'),
 ('장치', 'Noun'),
 ('이', 'Noun'),
 ('램', 'Noun'),
 ('밸브', 'Noun'),
 ('포함', 'Noun'),
 ('유압부', 'Noun'),
 ('유량', 'Noun'),
 ('감지', 'Noun'),
 ('장치', 'Noun'),
 ('비닐봉투', 'Noun'),
 ('고정', 'Noun'),
 ('구가', 'Noun'),
 ('구비', 'Noun'),
 ('물품', 'Noun'),
 ('수거', 'Noun'),
 ('함', 'Noun'),
 ('오일', 'Noun'),
 ('회로', 'Noun'),
 ('및', 'Noun'),
 ('오일', 'Noun'),
 ('회로', 'Noun'),
 ('구비', 'Noun'),
 ('무', 'Noun'),
 ('오일', 'Noun'),
 ('압축기', 'Noun'),
 ('엘리베이터', 'Noun'),
 ('용', 'Noun'),
 ('로', 'Noun'),
 ('가이드', 'Noun'),
 ('장치', 'Noun'),
 ('장식', 'Noun'),
 ('줄', 'Noun'),
 ('길이', 'Noun'),
 ('조절', 'Noun'),
 ('장신구', 'Noun'),
 ('착즙', 'Noun'),
 ('주스', 'Noun'),
 ('기용', 'Noun'),
 ('스', 'Noun'),
 ('크류', 'Noun'),
 ('및', 'Noun'),
 ('사용', 'Noun'),
 ('착즙', 'N